In [1]:
import os
import numpy as np
import pandas as pd
import geopandas as gpd
import datetime
import json

import matplotlib.pyplot as plt
from cartoframes.viz import *

import pickle
def load_graph_data(pkl_filename):
    sensor_ids, sensor_id_to_ind, adj_mx = load_pickle(pkl_filename)
    return sensor_ids, sensor_id_to_ind, adj_mx

def load_pickle(pickle_file):
    try:
        with open(pickle_file, 'rb') as f:
            pickle_data = pickle.load(f)
    except UnicodeDecodeError as e:
        with open(pickle_file, 'rb') as f:
            pickle_data = pickle.load(f, encoding='latin1')
    except Exception as e:
        print('Unable to load data ', pickle_file, ':', e)
        raise
    return pickle_data

In [2]:
import pandas as pd

meta_df_list = []
for fname in os.listdir('pems-output/metr-la'):
    mdf = pd.read_excel(f'pems-output/metr-la/{fname}')
    meta_df_list.append(mdf)
meta_df = pd.concat(meta_df_list)

In [3]:
meta_df

Fwy  District       County      City    CA PM  Abs PM  Length      ID  \
0   SR126-E         7  Los Angeles       NaN      4.9  39.398     NaN  775962   
1   SR126-E         7  Los Angeles       NaN      4.9  39.398     NaN  775963   
2   SR126-E         7  Los Angeles       NaN      4.9  39.398     NaN  775976   
3   SR126-E         7  Los Angeles       NaN      4.9  39.398   2.500  775975   
4   SR126-E         7  Los Angeles       NaN      4.9  39.398   1.076  775961   
..      ...       ...          ...       ...      ...     ...     ...     ...   
30    SR2-E         7  Los Angeles  Glendale    R21.5  14.062   0.913  767609   
31    SR2-E         7  Los Angeles  Glendale  R22.626  15.188     NaN  768235   
32    SR2-E         7  Los Angeles  Glendale  R22.626  15.188   3.063  768238   
33    SR2-E         7  Los Angeles  Glendale  R22.626  15.188     NaN  768246   
34    SR2-E         7  Los Angeles  Glendale  R22.636  15.198     NaN  768242   

                    Name  Lanes      Type Sensor Type HOV MS ID  IRM  
0     COMMERCE CENTER DR      1  Off Ramp         NaN  No  2695  NaN  
1     COMMERCE CENTER DR      1   On Ramp         NaN  No  2695  NaN  
2   COMMERCE CENTER DR.2      1   On Ramp         NaN  No  2696  NaN  
3   COMMERCE CENTER DR.2      4  Mainline         NaN  No  2696  NaN  
4     COMMERCE CENTER DR      3  Mainline         NaN  No  2695  NaN  
..                   ...    ...       ...         ...  ..   ...  ...  
30             FERN LANE      5  Mainline       loops  No  2473  NaN  
31     EB-NB 2 TO WB 210      3   Fwy-Fwy       loops  No  4472  NaN  
32          VERDUGO BLVD      2  Mainline       loops  No  4472  NaN  
33          VERDUGO BLVD      2  Off Ramp       loops  No  4472  NaN  
34     EB-NB 2 TO EB 210      2   Fwy-Fwy       loops  No  4472  NaN  

[10622 rows x 15 columns]

In [4]:
flist = os.listdir('california-vds')
item_list = []
for fname in sorted(flist):
    if fname[-4:] != 'json':
        continue
    print(fname)
    with open('california-vds/' + fname) as fp:
        json_data = json.load(fp)

        for item in json_data['matches']:
            item_list.append({
                'ID': str(int(item['ID'])),
                'lat': item['PT'][0],
                'lng': item['PT'][1]
            })
vds_df = pd.DataFrame(item_list).drop_duplicates('ID')

exact_id2loc = dict()
for _, item in vds_df.iterrows():
    exact_id2loc[item['ID']] = item.lat, item.lng

california-vds-10.json
california-vds-11.json
california-vds-12.json
california-vds-13.json
california-vds-14.json
california-vds-15.json
california-vds-17.json
california-vds-2.json
california-vds-3.json
california-vds-4.json
california-vds-5.json
california-vds-6.json
california-vds-7.json
california-vds-8.json
california-vds-9.json
california-vds.json


# Pemsd7

In [5]:
d7_sensors = pd.read_csv('pemsd7/PeMSD7_M_Station_Info.csv', index_col=0)
# d7_sensors = d7_sensors.set_index('index')
# d7_sensors.columns = ['sid', 'lat', 'lng']

In [6]:
d7_sensors

ID  Fwy Dir  District   Latitude   Longitude
0    716939    5   S         7  34.041407 -118.218373
1    759700    5   S         7  34.020961 -118.195456
2    716925    5   N         7  33.995023 -118.144513
3    715930    5   N         7  33.971763 -118.122905
4    715938    5   N         7  34.002541 -118.150997
..      ...  ...  ..       ...        ...         ...
223  766337  110   S         7  33.855273 -118.284900
224  763272  110   S         7  33.968828 -118.281010
225  763532  110   N         7  33.845433 -118.285155
226  763522  110   N         7  33.811070 -118.287268
227  763275  110   S         7  33.968828 -118.281010

[228 rows x 6 columns]

In [9]:
sensor_df = d7_sensors
sensor_gdf = gpd.GeoDataFrame(
    sensor_df, geometry=gpd.points_from_xy(x=sensor_df.Longitude, y=sensor_df.Latitude)
)
sensor_gdf.crs = 'epsg:4326'

In [20]:
sensor_gdf['sid'] = sensor_gdf['ID']
sensor_gdf['Fwy2'] = sensor_gdf['Fwy'].astype(str) + sensor_gdf['Dir']

In [14]:
from cartoframes.viz import Layer, color_category_style
Layer(sensor_gdf, color_category_style('Fwy2'))

# OSM load

In [15]:
from cartoframes.viz import Layer, popup_element, color_category_style, basic_style

In [16]:
import osmnx as ox

graph = ox.load_graphml(filepath=f'../graph_generation/osm_graph/pemsd7-drive.graphml')

In [17]:
gdf_nodes, gdf_edges = ox.graph_to_gdfs(graph)
gdf_nodes['osmidn'] = gdf_nodes.index
gdf_nodes['osmidstr'] = gdf_nodes['osmidn'].astype(str)

fgdf_edges = gdf_edges.reset_index()
cond = np.array([str(type(s)) for s in fgdf_edges['highway']]) == "<class 'str'>"
fgdf_edges = fgdf_edges[cond]

fmotorway = fgdf_edges[fgdf_edges['highway'].isin(['motorway'])]
fgdf_nodes = gdf_nodes[gdf_nodes.index.isin(set(fmotorway['u'].tolist() + fmotorway['v'].tolist()))]

In [27]:
mygraph = dict()
osmidpos = {osmidstr: (x, y) for osmidstr, y, x in zip(fgdf_nodes['osmidstr'], fgdf_nodes['y'], fgdf_nodes['x'])}
ffgdf_edges = fgdf_edges[fgdf_edges['u'].astype(str).isin(osmidpos) & fgdf_edges['v'].astype(str).isin(osmidpos)]

for _, item in ffgdf_edges.iterrows():
    us = str(item['u'])
    vs = str(item['v'])
    dist = item['length']
    
    mygraph.setdefault(us, {'pos': osmidpos[us]})
    mygraph.setdefault(vs, {'pos': osmidpos[vs]})
    mygraph[us][vs] = dist

import heapq
from typing import Dict, List

distances = {}
            
        
def a_star(graph: Dict[str, Dict[str, float]], 
           start: str, end: str) -> List[str]:
    # Heuristic function for estimating the distance between two nodes
    def h(node):
        if (node, end) not in distances:
            # In this example, we use a simple heuristic that assumes
            # a straight-line distance between nodes, ignoring obstacles
            x1, y1 = graph[node]['pos']
            x2, y2 = graph[end]['pos']
            distances[(node, end)] = ((x1 - x2) ** 2 + (y1 - y2) ** 2) ** 0.5
            distances[(end, node)] = ((x1 - x2) ** 2 + (y1 - y2) ** 2) ** 0.5
        return distances[(node, end)]
    
    # Initialize distance and previous node dictionaries
    g_score = {node: float('inf') for node in graph}
    g_score[start] = 0
    f_score = {node: float('inf') for node in graph}
    f_score[start] = h(start)
    prev = {node: None for node in graph}
    
    # Initialize heap with start node and its f score
    heap = [(f_score[start], start)]
    
    while heap:
        # Pop the node with the smallest f score from the heap
        (f, curr_node) = heapq.heappop(heap)
        
        # If we have reached the end node, return the shortest path
        if curr_node == end:
            path = []
            while curr_node is not None:
                path.append(curr_node)
                curr_node = prev[curr_node]
                
            return path[::-1]
        
        # Otherwise, update the f and g scores of all adjacent nodes
        for neighbor, weight in graph[curr_node].items():
            # Check if there is an edge between the current node and the neighbor
            if neighbor not in g_score:
                continue
                
            new_g_score = g_score[curr_node] + weight
            if new_g_score < g_score[neighbor]:
                g_score[neighbor] = new_g_score
                f_score[neighbor] = new_g_score + h(neighbor)
                prev[neighbor] = curr_node
                heapq.heappush(heap, (f_score[neighbor], neighbor))
    
    # If we get here, there is no path from start to end
    return None

# # Example graph with node positions
# graph = {
#     'A': {'B': 2, 'C': 1, 'pos': (0, 0)},
#     'B': {'C': 2, 'D': 3, 'pos': (1, 1)},
#     'C': {'D': 4, 'E': 3, 'pos': (1, -1)},
#     'D': {'E': 2, 'pos': (2, 0)},
#     'E': {'F': 3, 'pos': (3, -1)},
#     'F': {'pos': (4, 0)},
# }

# Find the shortest path from A to F using A* algorithm
# path = a_star(mygraph, 'A', 'F')
# print(path)  # Output: ['A', 'C', 'E', 'F']


In [21]:
Map([
    Layer(fgdf_nodes, basic_style(color='black'), popup_click=[
        popup_element('osmidstr')]),
    Layer(fmotorway, encode_data=False),
    Layer(sensor_gdf, color_category_style('Fwy2'), popup_click=[
        popup_element('sid')]),
])

In [22]:
sorted(sensor_gdf['Fwy2'].unique())

['105E',
 '105W',
 '10E',
 '10W',
 '110N',
 '110S',
 '405N',
 '405S',
 '5N',
 '5S',
 '605N',
 '605S',
 '60E',
 '60W',
 '710N',
 '710S',
 '91E',
 '91W']

In [100]:
fwy_path_dict = {
'105E': ('272463436', '359145741'),
'105W': ('359033574', '668233'),
'10E': ('122441204', '271054397'),
'10W': ('1613371627', '333174204'),
'110N': ('292696970', '1613486973'),
'110S': ('269633216', '64159237'),
'405N': ('298568672', '1613371665'),
'405S': ('2489818538', '297639932'),
'5N': ('21063546', '26666239'),
'5S': ('1614922775', '111656859'), # most deviant
'605N': ('18308824', '8783794235'),
'605S': ('122496511', '298153906'),
'60E': ('1613525086', '1154073355'),
'60W': ('268902455', '317639334'),
'710N': ('790301033', '663113132'),
'710S': ('253011611', '790301018'),
'91E': ('2500688506', '1955318098'),
'91W': ('1712608468', '1839471555')
    
}

In [101]:
key = '91W'
Map([
    Layer(fmotorway, encode_data=False),
    Layer(fgdf_nodes, basic_style(color='grey'), popup_click=[
        popup_element('osmidstr')]),
    Layer(sensor_gdf[sensor_gdf['Fwy2'] == key], basic_style(color='red'), popup_click=[
        popup_element('sid')]),
])

In [102]:
path = a_star(mygraph, fwy_path_dict[key][0], fwy_path_dict[key][1])
fgdf_tmp = fgdf_edges[fgdf_edges['u'].astype(str).isin(path) & fgdf_edges['v'].astype(str).isin(path)].copy()

Map([
    Layer(fgdf_tmp),
    Layer(sensor_gdf[sensor_gdf['Fwy2'] == key], basic_style(color='red'), popup_click=[
        popup_element('sid')]),
])


In [103]:
df_list = []
for uid in fwy_path_dict:
    path = a_star(mygraph, fwy_path_dict[uid][0], fwy_path_dict[uid][1])
    print(uid)
    fgdf_tmp = fgdf_edges[fgdf_edges['u'].astype(str).isin(path) & fgdf_edges['v'].astype(str).isin(path)].copy()
    fgdf_tmp['pathid'] = uid
    df_list.append(fgdf_tmp)

# adf = pd.concat(df_list)
agdf = gpd.GeoDataFrame(pd.concat(df_list))

105E
105W
10E
10W
110N
110S
405N
405S
5N
5S
605N
605S
60E
60W
710N
710S
91E
91W


In [108]:
from shapely.ops import linemerge
from shapely.geometry import LineString
from shapely.geometry import Point, LineString
from shapely.ops import nearest_points


sid2osmpath = []
# df_list = []

count = 0
fgdf_tmp_list = []

new_items = []
for uid in fwy_path_dict:
    path = a_star(mygraph, fwy_path_dict[uid][0], fwy_path_dict[uid][1])
    print(uid)
    fgdf_tmp = fgdf_edges[fgdf_edges['u'].astype(str).isin(path) & fgdf_edges['v'].astype(str).isin(path)].copy()
    fgdf_tmp['pathid'] = uid
    
    fgdf_tmp_list.append(fgdf_tmp)
    #     df_list.append(fgdf_tmp)

    # Merge the LineString objects into one LineString
    merged_line = linemerge(fgdf_tmp.geometry.tolist())

    # Print the resulting LineString
#     print(merged_line)
    
    for _, item in sensor_gdf[sensor_gdf['Fwy2'] == uid].iterrows():    
        closest_point_on_line, closest_point_on_point = nearest_points(merged_line, item.geometry)
        nitem = dict(item)
        nitem['geometry'] = closest_point_on_line
        new_items.append(nitem)
        
        clineitem = fgdf_tmp.iloc[fgdf_tmp.distance(item.geometry).argmin()]
        print(item['sid'], clineitem['u'], clineitem['v'])
        opitem = {
            'sid': str(item['sid']), 
            'fwy': item['Fwy2'],
            'lat': float(closest_point_on_line.y),
            'lng': float(closest_point_on_line.x), 
            'u': str(clineitem['u']), 
            'v': str(clineitem['v'])
        }
        sid2osmpath.append(opitem)
        
        count += 1
        
ngdf = gpd.GeoDataFrame(new_items)


fgdf_tmp_list = pd.concat(fgdf_tmp_list)

assert count == len(sensor_gdf)

105E
760130 306267185 1922406190
760166 306267771 306267886
760100 148811042 4013050931
760289 384342267 384342248
773656 144470939 122463910
760112 4013050931 206191520
716453 384377566 384342266
760226 293918240 322927827
765476 306267771 306267886
760167 306267771 306267886
760178 23964236 279645118
716470 359033520 359145741
760139 306267886 23964236
760110 4013050931 206191520
760074 122463910 1834760942
767838 272463436 144470939
105W


/tmp/ipykernel_3204736/1295897990.py:35: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  clineitem = fgdf_tmp.iloc[fgdf_tmp.distance(item.geometry).argmin()]
/tmp/ipykernel_3204736/1295897990.py:35: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  clineitem = fgdf_tmp.iloc[fgdf_tmp.distance(item.geometry).argmin()]


760442 452589520 668233
760572 384451875 384258477
716459 384454290 384443318
760369 384342345 384405132
763716 384448114 293917173
760375 384342345 384405132
760490 306268304 306264295
10E


/tmp/ipykernel_3204736/1295897990.py:35: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  clineitem = fgdf_tmp.iloc[fgdf_tmp.distance(item.geometry).argmin()]


718419 277328438 38724146
718410 18166124 24960499
717032 1613525130 1614655923
737237 122441204 1613371542
716057 1613324259 277327792
763458 1614922690 1614922653
763963 1613580518 653721
763346 277327730 1613324238
763453 1614922728 807656180
768584 1614655282 864284594
717011 1614655282 864284594
737158 72260323 271054397
717016 298043765 298044182
718335 1614656079 1614656074
10W


...

/tmp/ipykernel_3204736/1295897990.py:35: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  clineitem = fgdf_tmp.iloc[fgdf_tmp.distance(item.geometry).argmin()]


718002 29414060 36855747
718493 384383330 29414076
718018 25678982 1623240479
761761 384383330 29414076
718321 10565341 317625935
91E


/tmp/ipykernel_3204736/1295897990.py:35: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  clineitem = fgdf_tmp.iloc[fgdf_tmp.distance(item.geometry).argmin()]


768914 29098630 1376691463
717439 681307247 1711593967
717393 36220304 1376691468
768229 401422227 401422488
717434 303604048 303604103
717402 1839471546 303461056
717383 317767271 317765555
773381 36220300 36220304
716272 282786350 282786410
716273 1376691457 1775682962
717376 1955318169 1779417938
717436 303602719 681307247
717367 1840723952 1840723960
716296 1839471549 1839471546
717390 1715660197 36220294
759992 681307274 128196702
759967 1839471546 303461056
759975 303604048 303604103
768898 303465244 303465912
717426 303465244 303465912
773363 128196702 1955318098
765467 1877394471 1877394481
91W
717435 681307240 401422586
759990 1711614810 1711593986
766555 401422234 1711614810
717416 15258878 297838817
717404 1361122125 303461105
768228 401422234 1711614810
717424 1341338460 303465286
717433 303604420 303604334
759989 681307240 401422586
717410 1877394498 1877394483
773365 1712616451 26666214
717440 1711614810 1711593986


/tmp/ipykernel_3204736/1295897990.py:35: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  clineitem = fgdf_tmp.iloc[fgdf_tmp.distance(item.geometry).argmin()]


In [110]:
gpd.GeoDataFrame(sid2osmpath).to_csv('corrected-pemsd7-sensorid-osm-path-uv.csv', index=None)

In [112]:
category_order = list(fwy_path_dict.keys())
Map([
    Layer(agdf, color_category_style('pathid', cat=category_order),
          popup_click=[
              popup_element('pathid')], 
          popup_hover=[
              popup_element('pathid')]
          
         ),
    Layer(ngdf, color_category_style('Fwy2', cat=category_order), 
          popup_click=[
                popup_element('sid'),
              popup_element('Fwy2')], 
          popup_hover=[
                popup_element('sid'),
              popup_element('Fwy2')]),
])